<a href="https://colab.research.google.com/github/meido07/SQL-R-Python-Java-codes/blob/master/Reinforcement_Learning_for_Stock_Market_Trading_Yahoo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Stage 1: Installing dependencies and environment setup


In [0]:
!pip install tensorflow-gpu==2.0.0.alpha0

     |████████████████████████████████| 332.1MB 54kB/s 
     |████████████████████████████████| 419kB 44.2MB/s 
     |████████████████████████████████| 3.0MB 32.3MB/s 


In [0]:
!pip install pandas-datareader

## Stage 2: Importing project dependencies

In [0]:
import math
import random
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import pandas_datareader as data_reader

from tqdm import tqdm_notebook, tqdm
from collections import deque

/usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or 

In [0]:
tf.__version__

'2.0.0-alpha0'

## Stage 3: Building the AI Trader network

In [0]:
class AI_Trader():
  
  def __init__(self, state_size, action_space=3, model_name="AITrader"): #Stay, Buy, Sell
    
    self.state_size = state_size
    self.action_space = action_space
    self.memory = deque(maxlen=2000)
    self.inventory = []
    self.model_name = model_name
    
    self.gamma = 0.95
    self.epsilon = 1.0
    self.epsilon_final = 0.01
    self.epsilon_decay = 0.995
    
    self.model = self.model_builder()
    
  def model_builder(self):
    
    model = tf.keras.models.Sequential()
    
    model.add(tf.keras.layers.Dense(units=32, activation='relu', input_dim=self.state_size))
    
    model.add(tf.keras.layers.Dense(units=64, activation='relu'))
    
    model.add(tf.keras.layers.Dense(units=128, activation='relu'))
    
    model.add(tf.keras.layers.Dense(units=self.action_space, activation='linear'))
    
    model.compile(loss='mse', optimizer=tf.keras.optimizers.Adam(lr=0.001))
    
    return model
  
  def trade(self, state):
    
    if random.random() <= self.epsilon:
      return random.randrange(self.action_space)
    
    actions = self.model.predict(state)
    return np.argmax(actions[0])
  
  
  def batch_train(self, batch_size):
    
    batch = []
    for i in range(len(self.memory) - batch_size + 1, len(self.memory)):
      batch.append(self.memory[i])
      
    for state, action, reward, next_state, done in batch:
      reward = reward
      if not done:
        reward = reward + self.gamma * np.amax(self.model.predict(next_state)[0])
        
      target = self.model.predict(state)
      target[0][action] = reward
      
      self.model.fit(state, target, epochs=1, verbose=0)
      
    if self.epsilon > self.epsilon_final:
      self.epsilon *= self.epsilon_decay

## Stage 4: Dataset preprocessing

### Defining helper functions

#### Sigmoid

In [0]:
def sigmoid(x):
  return 1 / (1 + math.exp(-x))

#### Price format function

In [0]:
def stocks_price_format(n):
  if n < 0:
    return "- $ {0:2f}".format(abs(n))
  else:
    return "$ {0:2f}".format(abs(n))

#### Dataset loader

In [0]:
def dataset_loader(stock_name):
  
  #Complete the dataset loader function

  dataset = data_reader.DataReader(stock_name, data_source="yahoo")
  #dataset = data_reader.DataReader("AAPL", data_source="yahoo")
  
  start_date = str(dataset.index[0]).split()[0]
  end_date = str(dataset.index[-1]).split()[0]
  
  close = dataset['Close']

  return close

In [0]:
#dataset = data_reader.DataReader("AAPL", data_source="yahoo")

In [0]:
#dataset

High         Low  ...       Volume   Adj Close
Date                                ...                         
2010-01-04   30.642857   30.340000  ...  123432400.0   26.681330
2010-01-05   30.798571   30.464285  ...  150476200.0   26.727465
2010-01-06   30.747143   30.107143  ...  138040000.0   26.302330
2010-01-07   30.285715   29.864286  ...  119282800.0   26.253704
2010-01-08   30.285715   29.865715  ...  111902700.0   26.428249
...                ...         ...  ...          ...         ...
2019-10-18  237.580002  234.289993  ...   24358400.0  236.410004
2019-10-21  240.990005  237.320007  ...   21811800.0  240.509995
2019-10-22  242.199997  239.619995  ...   20573400.0  239.960007
2019-10-23  243.240005  241.220001  ...   18957200.0  243.179993
2019-10-24  244.800003  241.809998  ...   13833739.0  243.054993

[2470 rows x 6 columns]

In [0]:
dataset.index[0]

Timestamp('2010-01-04 00:00:00')

### State creator

In [0]:
def state_creator(data, timestep, window_size):
  
  starting_id = timestep - window_size + 1
  
  if starting_id >= 0:
    windowed_data = data[starting_id:timestep+1]
  else:
    windowed_data = - starting_id * [data[0]] + list(data[0:timestep+1])
    
  state = []
  for i in range(window_size - 1):
    state.append(sigmoid(windowed_data[i+1] - windowed_data[i]))
    
  return np.array([state])

### Loading a dataset

In [0]:
stock_name = "AAPL"
data = dataset_loader(stock_name)

In [0]:
data

Date
2010-01-04     30.572857
2010-01-05     30.625713
2010-01-06     30.138571
2010-01-07     30.082857
2010-01-08     30.282858
                 ...    
2019-10-18    236.410004
2019-10-21    240.509995
2019-10-22    239.960007
2019-10-23    243.179993
2019-10-24    243.070007
Name: Close, Length: 2470, dtype: float64

## Stage 5: Training the AI Trader

### Setting hyper parameters

In [0]:
window_size = 10
episodes = 1000

batch_size = 32
data_samples = len(data) - 1

### Defining the Trader model

In [0]:
trader = AI_Trader(window_size)

In [0]:
trader.model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 32)                352       
_________________________________________________________________
dense_1 (Dense)              (None, 64)                2112      
_________________________________________________________________
dense_2 (Dense)              (None, 128)               8320      
_________________________________________________________________
dense_3 (Dense)              (None, 3)                 387       
Total params: 11,171
Trainable params: 11,171
Non-trainable params: 0
_________________________________________________________________


### Training loop

In [0]:
for episode in range(1, episodes + 1):
  
  print("Episode: {}/{}".format(episode, episodes))
  
  state = state_creator(data, 0, window_size + 1)
  
  total_profit = 0
  trader.inventory = []
  
  for t in tqdm(range(data_samples)):
    
    action = trader.trade(state)
    
    next_state = state_creator(data, t+1, window_size + 1)
    reward = 0
    
    if action == 1: #Buying
      trader.inventory.append(data[t])
      print("AI Trader bought: ", stocks_price_format(data[t]))
      
    elif action == 2 and len(trader.inventory) > 0: #Selling
      buy_price = trader.inventory.pop(0)
      
      reward = max(data[t] - buy_price, 0)
      total_profit += data[t] - buy_price
      print("AI Trader sold: ", stocks_price_format(data[t]), " Profit: " + stocks_price_format(data[t] - buy_price) )
      
    if t == data_samples - 1:
      done = True
    else:
      done = False
      
    trader.memory.append((state, action, reward, next_state, done))
    
    state = next_state
    
    if done:
      print("########################")
      print("TOTAL PROFIT: {}".format(total_profit))
      print("########################")
    
    if len(trader.memory) > batch_size:
      trader.batch_train(batch_size)
      
  if episode % 10 == 0:
    trader.model.save("ai_trader_{}.h5".format(episode))
    

  0%|          | 0/2469 [00:00<?, ?it/s]

Episode: 1/1000
AI Trader bought:  $ 30.572857
AI Trader bought:  $ 30.625713
AI Trader sold:  $ 30.138571  Profit: - $ 0.434286
AI Trader bought:  $ 30.282858
AI Trader bought:  $ 30.015715
AI Trader sold:  $ 30.092857  Profit: - $ 0.532856
AI Trader sold:  $ 29.918571  Profit: - $ 0.364286
AI Trader sold:  $ 29.418571  Profit: - $ 0.597143
AI Trader bought:  $ 28.250000
AI Trader bought:  $ 29.420000
AI Trader bought:  $ 29.697144
AI Trader bought:  $ 28.469999
AI Trader bought:  $ 27.437143
AI Trader sold:  $ 27.980000  Profit: - $ 0.270000
AI Trader sold:  $ 28.461428  Profit: - $ 0.958572
AI Trader bought:  $ 27.922857
AI Trader sold:  $ 27.731428  Profit: - $ 1.965715
AI Trader sold:  $ 28.027143  Profit: - $ 0.442856
AI Trader sold:  $ 27.874287  Profit: $ 0.437143
AI Trader sold:  $ 28.381428  Profit: $ 0.458570
AI Trader bought:  $ 28.625713
AI Trader bought:  $ 29.057142
AI Trader bought:  $ 28.935715
AI Trader sold:  $ 28.809999  Profit: $ 0.184286


  1%|▏         | 33/2469 [00:01<02:02, 19.86it/s]

AI Trader sold:  $ 28.631428  Profit: - $ 0.425714


  1%|▏         | 34/2469 [00:01<04:43,  8.60it/s]

...

AI Trader sold:  $ 48.805714  Profit: $ 1.091427


 10%|█         | 259/2469 [01:07<09:52,  3.73it/s]

AI Trader sold:  $ 49.202858  Profit: $ 0.281429


 11%|█         | 276/2469 [01:11<09:16,  3.94it/s]

AI Trader bought:  $ 50.268570
Buffered data was truncated after reaching the output size limit.